In [1]:
import pandas as pd
import pyarrow.parquet as pq
import pyarrow as pa
import glob
import os
from tqdm import tqdm
tqdm.pandas()
pd.options.mode.chained_assignment = None

/home/yin/anaconda3/envs/py3/lib/python3.7/site-packages/tqdm/std.py:656: FutureWarning: The Panel class is removed from pandas. Accessing it from the top-level namespace will also be removed in the next version
  from pandas import Panel


In [26]:
df = pd.read_pickle('UK_Oxford_skill_processed_all.pkl')

In [56]:
df

JobID SICCode     JobDate    CanonCity  CanonCounty  \
1        26058507    None  2012-01-29      SALFORD  Oxfordshire   
2        27150342  221210  2012-03-16  WALLINGFORD  Oxfordshire   
2        27150342  221210  2012-03-16  WALLINGFORD  Oxfordshire   
2        27150342  221210  2012-03-16  WALLINGFORD  Oxfordshire   
2        27150342  221210  2012-03-16  WALLINGFORD  Oxfordshire   
...           ...     ...         ...          ...          ...   
207061  765272008    None  2019-01-14         None  Oxfordshire   
207061  765272008    None  2019-01-14         None  Oxfordshire   
207066  765272024    None  2019-01-14         None  Oxfordshire   
207066  765272024    None  2019-01-14         None  Oxfordshire   
207066  765272024    None  2019-01-14         None  Oxfordshire   

       LocalAuthorityDistrict  \
1            West Oxfordshire   
2           South Oxfordshire   
2           South Oxfordshire   
2           South Oxfordshire   
2           South Oxfordshire   
...                       ...   
207061                   None   
207061                   None   
207066                   None   
207066                   None   
207066                   None   

                                       CanonSkillClusters SOCCode       date  \
1          Business: Business Strategy;Specialised Skills    7220 2012-01-29   
2       Specialised Skills|Human Resources: Employee T...    2123 2012-03-16   
2       Specialised Skills|Human Resources: Employee T...    2123 2012-03-16   
2       Specialised Skills|Human Resources: Employee T...    2123 2012-03-16   
2       Specialised Skills|Human Resources: Employee T...    2123 2012-03-16   
...                                                   ...     ...        ...   
207061  Information Technology: Web Development;Specia...    2136 2019-01-14   
207061  Information Technology: Web Development;Specia...    2136 2019-01-14   
207066  Finance: General Accounting;Specialised Skills...    4129 2019-01-14   
207066  Finance: General Accounting;Specialised Skills...    4129 2019-01-14   
207066  Finance: General Accounting;Specialised Skills...    4129 2019-01-14   

                  CanonSkills  
1       Strategic Development  
2        Communication Skills  
2         Management Training  
2                   Mentoring  
2             Problem Solving  
...                       ...  
207061  Front-end Development  
207061             JavaScript  
207066             Accounting  
207066                Finance  
207066        Microsoft Excel  

[6901871 rows x 10 columns]

In [3]:
## if you want to pritn the columns
# for col in df.columns: 
#     print(col) 

In [4]:
def select_df(df, start_date, end_date, 
              city = False, sic = False, soc = False, county = False):
    mask = (df['date'] >= start_date) & (df['date'] <= end_date)
    df = df.loc[mask]
    if city != False:
        df = df[(df['CanonCity'] == city)]
    if sic != False:
        df = df[(df['SICCode'].str[:4] == sic)]
    if soc != False:
        df = df[(df['SOCCode'].str[:3] == soc)]
    if county != False:
        df = df[(df['CanonCounty'] == county)]
        
    return df

### 1) Calculate frequency counts of CanonSkills for a sub-sampe of job ads tagged as 

In [19]:
start_date = '2012-01-01'
end_date = '2019-11-04'
county = 'Oxfordshire'

s1 = select_df(df, start_date = start_date
               , end_date = end_date, county = county)
skill_count_df1 = pd.DataFrame(s1['CanonSkills'].value_counts())
skill_count_df1['Percent'] = (skill_count_df1['CanonSkills']/skill_count_df1['CanonSkills'].sum())*100
skill_count_df1




CanonSkills   Percent
Communication Skills           273610  3.990336
Organisational Skills          128678  1.876644
Customer Service               121213  1.767774
Sales                          112977  1.647660
Teamwork / Collaboration       102318  1.492209
...                               ...       ...
Stripping Tools                     1  0.000015
Coding Accuracy                     1  0.000015
Toilet Installation                 1  0.000015
Euroclear                           1  0.000015
Oracle Waveset                      1  0.000015

[8713 rows x 2 columns]

### 2) Calculate frequency counts of CanonSkills for a sub-sampe of job ads tagged 
**for each sic**


In [23]:
# s2[(s2['SICCode']=='86')]['Count'].sum()
# # check answer
# 100*15373/309094

4.9735679113797095

In [9]:

s2 = s1.groupby(["CanonSkills", "SICCode"]).size(
).to_frame('Count').sort_values(['Count'],ascending=False).reset_index()

In [11]:
s2['Percent'] = s2.progress_apply(lambda x: 100*x['Count']/s2[(s2['SICCode']==x['SICCode'])]['Count'].sum(), axis=1)
skill_count_df2 = pd.DataFrame(s2)


  0%|          | 1393/342382 [00:31<2:06:39, 44.87it/s]


  1%|          | 2773/342382 [01:02<2:07:20, 44.45it/s]


  1%|          | 4153/342382 [01:33<2:07:03, 44.36it/s]


  2%|▏         | 5533/342382 [02:04<2:07:19, 44.09it/s]


  2%|▏         | 6913/342382 [02:35<2:07:58, 43.69it/s]


...

 99%|█████████▊| 337256/342382 [2:06:20<01:53, 45.25it/s]


 99%|█████████▉| 338596/342382 [2:06:50<01:25, 44.45it/s]


 99%|█████████▉| 339936/342382 [2:07:20<00:55, 43.83it/s]


100%|█████████▉| 341276/342382 [2:07:50<00:25, 44.10it/s]


100%|██████████| 342382/342382 [2:08:15<00:00, 44.49it/s]


In [12]:
skill_count_df2

CanonSkills  SICCode  Count    Percent
0              Communication Skills       86  15373   4.973568
1                          Research    85.42  14962   5.925498
2              Communication Skills    85.42  12103   4.793229
3              Communication Skills        C  11065   3.240278
4                          Teaching       85   9119  13.073085
...                             ...      ...    ...        ...
342377  Measles Mumps Rubella (MMR)     62.0      1   0.023708
342378  Measles Mumps Rubella (MMR)    64.19      1   0.012718
342379  Measles Mumps Rubella (MMR)  64.20/2      1   0.092851
342380  Measles Mumps Rubella (MMR)  68.20/9      1   0.013557
342381                virtual sales       86      1   0.000324

[342382 rows x 4 columns]

### 3) Calculate frequency counts of CanonSkills for a sub-sampe of job ads tagged as 
**for each soc**


In [6]:
s3 = s1.groupby(["CanonSkills", "SOCCode"]).size().to_frame('Count').sort_values(['Count'],ascending=False).reset_index()

In [7]:
s3['Percent'] = s3.progress_apply(lambda x: 100*x['Count']/s3[(s3['SOCCode']==x['SOCCode'])]['Count'].sum(), axis=1)
skill_count_df3 = pd.DataFrame(s3)
skill_count_df3

100%|██████████| 442138/442138 [3:38:38<00:00, 33.70it/s]  


CanonSkills SOCCode  Count    Percent
0                       Sales    7129  25596   8.570195
1                     Cooking    5434  17508  17.473403
2        Software Development    2136  15157   2.604586
3        Communication Skills    2136  14332   2.462818
4                         SQL    2136  14006   2.406798
...                       ...     ...    ...        ...
442133  Oral Cancer knowledge    2137      1   0.000477
442134  Oral Cancer knowledge    2211      1   0.003102
442135  Oral Cancer knowledge    3218      1   0.007985
442136  Oral Cancer knowledge    5113      1   0.016664
442137          virtual sales    8212      1   0.004308

[442138 rows x 4 columns]

In [22]:
# s3[(s3['SOCCode']=='7129')]['Count'].sum()
# # check answer
# 100*25596/298663

8.570194500155694

### 4) Calculate frequency counts of CanonSkills for a sub-sampe of job ads tagged as 
**for each LocalAuthorityDistrict**


In [8]:
i = 3
eval("skill_count_df"+str(i)).to_csv('output_' + str(i) + '.csv')

In [9]:
s4 = s1.groupby(["CanonSkills", "LocalAuthorityDistrict"]).size().to_frame('Count').sort_values(['Count'],ascending=False).reset_index()


In [10]:
s4['Percent'] = s4.progress_apply(lambda x: 100*x['Count']/s4[(s4['LocalAuthorityDistrict']==x['LocalAuthorityDistrict'])]['Count'].sum(), axis=1)
skill_count_df4 = pd.DataFrame(s4)
skill_count_df4

100%|██████████| 32105/32105 [01:50<00:00, 290.01it/s]


CanonSkills LocalAuthorityDistrict   Count   Percent
0             Communication Skills                 Oxford  114209  3.977165
1            Organisational Skills                 Oxford   52727  1.836143
2                 Customer Service                 Oxford   47492  1.653841
3                            Sales                 Oxford   46983  1.636116
4                         Research                 Oxford   46714  1.626748
...                            ...                    ...     ...       ...
32100   Prevent And Treat Injuries                 Oxford       1  0.000035
32101              Survey Analysis      South Oxfordshire       1  0.000146
32102              Survey Analysis               Cherwell       1  0.000120
32103      Climate Change Research                 Oxford       1  0.000035
32104  Medicare/Medicaid Knowledge       West Oxfordshire       1  0.000266

[32105 rows x 4 columns]

In [25]:
# s4[(s4['LocalAuthorityDistrict']=='Oxford')]['Count'].sum()
# # check answer
# 100*114209/2871618

3.9771654864957666

### 5) Calculate frequency counts of CanonSkills for a sub-sampe of job ads tagged as 
**for each CanonCity**



In [11]:
i = 4
eval("skill_count_df"+str(i)).to_csv('output_' + str(i) + '.csv')

In [12]:
s5 = s1.groupby(["CanonSkills", "CanonCity"]).size().to_frame('Count').sort_values(['Count'],ascending=False).reset_index()


In [13]:
s5['Percent'] = s5.progress_apply(lambda x: 100*x['Count']/s5[(s5['CanonCity']==x['CanonCity'])]['Count'].sum(), axis=1)
skill_count_df5 = pd.DataFrame(s5)
skill_count_df5

100%|██████████| 113274/113274 [15:24<00:00, 122.48it/s]


CanonSkills CanonCity  Count   Percent
0        Communication Skills    OXFORD  91958  3.907412
1       Organisational Skills    OXFORD  41614  1.768231
2                       Sales    OXFORD  40472  1.719706
3            Customer Service    OXFORD  37691  1.601538
4                    Research    OXFORD  35722  1.517873
...                       ...       ...    ...       ...
113269                 Drupal  BLEWBURY      1  0.009630
113270           Drug Therapy    WITNEY      1  0.000594
113271   Positive Disposition   Tackley      1  0.552486
113272           Drug Therapy  ABINGDON      1  0.000238
113273           Property Tax  Bicester      1  0.001500

[113274 rows x 4 columns]

### 6) Calculate frequency counts of CanonSkills from 2012 - 2019


In [14]:
i = 5
eval("skill_count_df"+str(i)).to_csv('output_' + str(i) + '.csv')

In [15]:
start_date = '2012-01-01'
end_date = '2019-11-04'
county = 'Oxfordshire'

s1 = select_df(df, start_date = start_date
               , end_date = end_date, county = county)
s1['year'] = s1['date'].dt.year

skill_count_df6 = pd.DataFrame(s1.groupby(['year', 'CanonSkills']).size().to_frame('count').sort_values(['year', 'count'],ascending=False)).reset_index()
skill_count_df6

year                CanonSkills  count
0      2019       Communication Skills  28645
1      2019      Organisational Skills  14436
2      2019           Customer Service  14107
3      2019   Teamwork / Collaboration  13122
4      2019          Detail-Orientated  11232
...     ...                        ...    ...
44627  2012  X-Ray Computed Tomography      1
44628  2012      X-Ray Crystallography      1
44629  2012                     X/Open      1
44630  2012                       cDNA      1
44631  2012                  e-Science      1

[44632 rows x 3 columns]

In [ ]:
## skill_count_df6
skill_count_df6_reshape = skill_count_df6.pivot(columns='year',index='CanonSkills', values='count')

skill_count_df6_reshape.to_csv('skill_count_df6_reshape.csv')

skill_count_df6_reshape.pct_change(axis='columns').to_csv('skill_count_df6_reshape_percent.csv')

### 7) Calculate frequency counts of CanonSkills from Jan to Oct in 2019


In [16]:
start_date = '2019-01-01'
end_date = '2019-10-30'
county = 'Oxfordshire'

s1 = select_df(df, start_date = start_date
               , end_date = end_date, county = county)
s1['month'] = s1['date'].dt.month

skill_count_df7 = pd.DataFrame(s1.groupby(['month', 'CanonSkills']).size().to_frame('count').sort_values(['month', 'count'],ascending=False)).reset_index()
skill_count_df7

month               CanonSkills  count
0         10      Communication Skills   2803
1         10     Organisational Skills   1353
2         10          Customer Service   1294
3         10  Teamwork / Collaboration   1270
4         10                  Research   1161
...      ...                       ...    ...
33766      1                    Xilinx      1
33767      1                  Zoonotic      1
33768      1               iOS Testing      1
33769      1                 iOS Tools      1
33770      1              trigonometry      1

[33771 rows x 3 columns]

In [55]:
## skill_count_df6
skill_count_df7_reshape = skill_count_df7.pivot(columns='month',index='CanonSkills', values='count')

skill_count_df7_reshape.to_csv('skill_count_df7_reshape.csv')

skill_count_df7_reshape.pct_change(axis='columns').to_csv('skill_count_df7_reshape_percent.csv')

month                                      1         2         3         4   \
CanonSkills                                                                   
.NET                                      NaN -0.110236 -0.159292 -0.010526   
360 Feedback                              NaN  0.000000  0.000000  0.000000   
3D Animation                              NaN  0.000000 -0.857143  3.000000   
3D Modelling / Design                     NaN -0.482759  0.200000  0.000000   
3D Printing / Additive Manufacturing (AM) NaN  1.250000 -0.222222  0.285714   
...                                        ..       ...       ...       ...   
jQuery UI                                 NaN -0.666667  0.000000  0.000000   
mHealth                                   NaN       NaN  0.000000  0.000000   
qPCR                                      NaN -0.529412  0.125000  0.777778   
shRNA                                     NaN       NaN  0.000000  0.000000   
trigonometry                              NaN  0.000000  0.000000  0.000000   

month                                            5         6         7   \
CanonSkills                                                               
.NET                                      -0.053191 -0.022472  0.310345   
360 Feedback                               0.000000  0.000000  0.000000   
3D Animation                               0.500000 -0.333333 -0.750000   
3D Modelling / Design                      0.277778  0.173913 -0.333333   
3D Printing / Additive Manufacturing (AM)  0.222222 -0.181818  0.555556   
...                                             ...       ...       ...   
jQuery UI                                  0.000000  0.000000  0.000000   
mHealth                                    0.000000  0.000000  0.000000   
qPCR                                      -0.125000  0.214286 -0.647059   
shRNA                                      0.000000  0.000000  0.000000   
trigonometry                               2.000000  0.000000 -0.333333   

month                                            8         9         10  
CanonSkills                                                              
.NET                                      -0.008772 -0.336283  0.546667  
360 Feedback                               0.000000  0.000000  0.000000  
3D Animation                               7.000000 -0.750000  0.000000  
3D Modelling / Design                      0.055556 -0.315789  1.461538  
3D Printing / Additive Manufacturing (AM) -0.571429 -0.166667  1.800000  
...                                             ...       ...       ...  
jQuery UI                                  0.000000  0.000000  0.000000  
mHealth                                    0.000000  0.000000  0.000000  
qPCR                                       0.333333  0.125000  0.000000  
shRNA                                      0.000000  1.000000  0.000000  
trigonometry                              -0.500000  0.000000  0.000000  

[5391 rows x 10 columns]

### 8) Calculate frequency counts of CanonSkills for a sub-sampe of job ads tagged as 
**for each soc & SIC & year**

In [75]:
start_date = '2012-01-01'
end_date = '2019-11-04'
county = 'Oxfordshire'

s1 = select_df(df, start_date = start_date
               , end_date = end_date, county = county)
s1['year'] = s1['date'].dt.year

skill_count_df8 = pd.DataFrame(s1.groupby(['year','CanonSkills', 'SOCCode', 'SICCode']).size().to_frame('count').sort_values(['year', 'CanonSkills','SOCCode', 'SICCode'],ascending=False)).reset_index()
skill_count_df8

year   CanonSkills SOCCode  SICCode  count
0        2019  trigonometry    5215    82.99      1
1        2019  trigonometry    4212  69.20/1      1
2        2019  trigonometry    3122  43.99/9      1
3        2019  trigonometry    2471    72.19      1
4        2019  trigonometry    2136  62.01/2      2
...       ...           ...     ...      ...    ...
1815723  2012          .NET    1131    20.42      1
1815724  2012          .NET    1122    49.10      1
1815725  2012          .NET    1121        C      2
1815726  2012          .NET    1121    56.30      1
1815727  2012          .NET    1121    25.94      1

[1815728 rows x 5 columns]

In [76]:
skill_count_df8 = skill_count_df8.pivot_table(
        values='count', 
        index=['CanonSkills', 'SOCCode', 'SICCode'], 
        columns='year')
skill_count_df8

year                           2012  2013  2014  2015  2016  2017  2018  2019
CanonSkills   SOCCode SICCode                                                
.NET          1115    38.21     NaN   1.0   NaN   NaN   NaN   NaN   NaN   NaN
                      58        NaN   NaN   2.0   NaN   NaN   NaN   NaN   NaN
                      58.11     NaN   NaN   1.0   NaN   NaN   NaN   NaN   NaN
                      58.19     NaN   NaN   NaN   1.0   NaN   NaN   NaN   NaN
                      74.30     NaN   NaN   NaN   1.0   NaN   NaN   NaN   NaN
...                             ...   ...   ...   ...   ...   ...   ...   ...
virtual sales 7129    62.02     NaN   NaN   NaN   NaN   NaN   1.0   NaN   NaN
                      68        NaN   5.0  13.0   NaN   1.0   NaN   NaN   NaN
              7130    47        1.0   NaN   NaN   NaN   NaN   NaN   NaN   NaN
              7219    47.11     NaN   NaN   1.0   NaN   NaN   NaN   NaN   NaN
              8149    41.20     NaN   NaN   1.0   NaN   NaN   NaN   NaN   NaN

[1222376 rows x 8 columns]

In [73]:
skill_count_df8.to_csv('skill_count_df8.csv')

In [72]:
skill_count_df8.pct_change(axis='columns').to_csv('skill_count_df8_percent.csv')

### 9) Calculate frequency counts of CanonSkills for a sub-sampe of job ads tagged as 
**for each soc & SIC & month in 2019**

In [78]:
start_date = '2019-01-01'
end_date = '2019-10-30'
county = 'Oxfordshire'

s1 = select_df(df, start_date = start_date
               , end_date = end_date, county = county)
s1['month'] = s1['date'].dt.month

skill_count_df9= pd.DataFrame(s1.groupby(['month','CanonSkills', 'SOCCode', 'SICCode']).size().to_frame('count').sort_values(['month', 'CanonSkills','SOCCode', 'SICCode'],ascending=False)).reset_index()

skill_count_df9= skill_count_df9.pivot_table(
        values='count', 
        index=['CanonSkills', 'SOCCode', 'SICCode'], 
        columns='month')
skill_count_df9

month                          1    2    3    4    5   6    7    8    9   10
CanonSkills  SOCCode SICCode                                                
.NET         1131    47.19    NaN  NaN  NaN  NaN  1.0 NaN  NaN  NaN  NaN NaN
                     64.30    NaN  NaN  NaN  NaN  NaN NaN  NaN  NaN  1.0 NaN
                     68       NaN  NaN  NaN  NaN  NaN NaN  NaN  1.0  NaN NaN
                     85.42    NaN  1.0  NaN  1.0  NaN NaN  NaN  NaN  NaN NaN
                     C        NaN  NaN  NaN  1.0  NaN NaN  1.0  NaN  NaN NaN
...                           ...  ...  ...  ...  ...  ..  ...  ...  ...  ..
trigonometry 2136    62.01/2  NaN  NaN  NaN  NaN  2.0 NaN  NaN  NaN  NaN NaN
             2471    72.19    NaN  NaN  1.0  NaN  NaN NaN  NaN  NaN  NaN NaN
             3122    43.99/9  1.0  NaN  NaN  NaN  NaN NaN  NaN  NaN  NaN NaN
             4212    69.20/1  NaN  NaN  NaN  NaN  NaN NaN  NaN  1.0  NaN NaN
             5215    82.99    NaN  NaN  NaN  NaN  NaN NaN  1.0  NaN  NaN NaN

[203550 rows x 10 columns]

In [79]:
skill_count_df9.to_csv('skill_count_df9_month.csv')
skill_count_df9.pct_change(axis='columns').to_csv('skill_count_df9_month_percent.csv')

In [ ]:
## all skill term year & month growth

In [81]:
start_date = '2012-01-01'
end_date = '2019-11-04'
county = 'Oxfordshire'

s1 = select_df(df, start_date = start_date
               , end_date = end_date, county = county)
s1['year'] = s1['date'].dt.year

skill_count_df10 = pd.DataFrame(s1.groupby(['year']).size().to_frame('count').sort_values(['count'],ascending=False)).reset_index()
skill_count_df10.to_csv('skill_count_df10_year.csv')
skill_count_df10

year    count
0  2017  1119623
1  2018  1056666
2  2016  1025053
3  2015   874988
4  2013   824091
5  2014   759267
6  2019   670730
7  2012   571453

In [82]:
start_date = '2019-01-01'
end_date = '2019-10-30'
county = 'Oxfordshire'

s1 = select_df(df, start_date = start_date
               , end_date = end_date, county = county)
s1['month'] = s1['date'].dt.month
skill_count_df11 = pd.DataFrame(s1.groupby(['month']).size().to_frame('count').sort_values(['count'],ascending=False)).reset_index()
skill_count_df11.to_csv('skill_count_df11_month.csv')
skill_count_df11


month  count
0      1  74858
1      7  71101
2      8  68591
3      2  68331
4      3  67345
5     10  66871
6      5  63470
7      6  62915
8      4  59158
9      9  58769

In [20]:
## Output to csv
for i in range(1,2):
    eval("skill_count_df"+str(i)).to_csv('output_' + str(i) + '.csv')

